# E10-3: A multi-resolution sinusoidal model

In this exercise you will implement a multi-resolution sine model by modifying the `sineModel()` function.

You have seen through several assignments that the choice of window size is an important tradeoff between time and frequency resolution. Longer windows have a better frequency resolution and can resolve two close sinusoids even at low frequencies, while smaller windows have a better time resolution leading to sharper onsets. So far, in all the analyses, we have only considered a single window length over the whole sound. As we know, analysis of signals with low frequency components needs longer windows as compared to signals with high frequency content. The optimal choice of window length is thus dependent on the frequency content of the signal. In other words, it is better to choose a longer window for the analysis of the low frequencies while a shorter window is sufficient for higher frequencies. In this exercise, you will explore the use of multiple window sizes for analysis in different frequency bands of the signals, what is called multi-resolution.

For each audio frame of `x` you should compute three different DFTs with three different window sizes and find the sinusoidal peaks for each of the DFTs. For example, you can choose window sizes `M1 = 4095, M2 = 2047, M3 = 1023`, to generate three windows w1, w2, w3. Choose N1, N2, N3 to be the power of two bigger than the corresponding window size. Then compute the spectra, `X1`, `X2`, and `X3` using `dftAnal()`. Define the frequency bands like `B1: 0 <= f < 1000Hz, B2: 1000 <= f < 5000, B3: 5000 <= f < 22050` and find the peaks of `B1` in `X1`, the ones of `B2` in `X2`, and the ones of `B3` in `X3`. From the peaks we finally re-synthesize the frame and generate the output `y`.

Complete `sineModelMultiRes()`, by copiying and modifying the code from `SineModel()`. The functions should take as input three windows with different sizes, three FFT sizes, and the values for the frequency bands. Write the code to implement the multi-resolution analysis as described above.

Choose two different polyphonic recordings from freesound that have both a relevant melodic and percussion components. Edit them and change their format as needed. Choose suitable set of parameters for their analysis. Experiment with different window sizes and fruequency bands for the two sounds such that you get both crisp onsets and good frequency resolution. Get the best posible base line reconstruction with `SineModel()` and the best with `sineModelMultiRes()`. Listen the sounds and visualize the information that might be needed to undertand the process.

Your explanation should include:

1. Freesound link to the two sounds chosen.
2. Explanation and justification of the band edges and the window sizes for each sound.
3. Observations about the advantages of a multi-resolution analysis (comment on the time-frequency resolution, computational complexity and extensions to HPR and HPS models).
4. Challenges you might face if you were to extend it to HPR and HPS models (mainly in sinusoid tracking and F0 estimation).
5. Further methods to improving the time-frequency resolution trade-off.


In [ ]:
#if want to run this notebook in google colab you should uncomment the following commands
!pip install sms-tools
!git clone https://github.com/MTG/sms-tools-materials.git
!pip install numpy==1.23.5
!pip install git+https://github.com/mtg/freesound-python.git
!pip install essentia

fatal: destination path 'sms-tools-materials' already exists and is not an empty directory.
  Cloning https://github.com/mtg/freesound-python.git to /tmp/pip-req-build-lueol2wf
  Running command git clone --filter=blob:none --quiet https://github.com/mtg/freesound-python.git /tmp/pip-req-build-lueol2wf
  Resolved https://github.com/mtg/freesound-python.git to commit 5be99a3689d17303c01cb122bbb0d5a96eba04f6
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.7/13.7 MB 94.5 MB/s eta 0:00:00


In [ ]:
import sys, os
from scipy.signal import get_window
import numpy as np
#from scipy.signal import blackmanharris, triang
from scipy.signal.windows import blackmanharris, triang
from scipy.fftpack import ifft, fftshift
import math
from smstools.models import dftModel as DFT
from smstools.models import utilFunctions as UF
from smstools.models import dftModel as DFT
from smstools.models import utilFunctions as UF
from smstools.models import sineModel as SM
import IPython.display as ipd

In [ ]:
import numpy as np
from scipy.signal import get_window
import essentia.standard as es

### your code here, start from copying the code from sineModel()

import numpy as np
from scipy.signal import get_window
import essentia.standard as es

### your code here, start from copying the code from sineModel()

def sineModelMultiRes(x, fs, w, N, t, B):
    """
    Analysis/syn  thesis of a sound using the sinusoidal model, without sine tracking
    Inputs:
        x: input array sound
        w: 3 analysis windows
        t: threshold in negative dB
        B: 3 frequency boundaries
    Output:
        y: output array sound
    """

    ### your code here, start from copying the code from sineModel()
    M1, M2, M3 = len(w[0]), len(w[1]), len(w[2])
    H = 256  # hop size
    pin = max(M1, M2, M3) // 2
    pend = len(x) - max(M1, M2, M3) // 2

    # Initialize y as a complex array to accommodate the output of SineModelSynth
    y = np.zeros(len(x), dtype=np.complex128)  # output buffer
    synth = es.SineModelSynth()

    while pin < pend:
        frame_peaks_freqs = []
        frame_peaks_mags = []

        for i, (win, fft_size, band) in enumerate(zip(w, N, B)):
            M = len(win)
            # Adjust start and end indices to handle window centering around pin
            start_index = pin - M // 2
            end_index = start_index + M

            if start_index < 0 or end_index > len(x):
                continue  # skip if window exceeds signal bounds

            x1 = x[start_index : end_index]
            if len(x1) < M:
                # This part should ideally not be reached if the start/end checks are correct
                # However, keeping it for robustness in case of edge cases not covered.
                x1 = np.append(x1, np.zeros(M - len(x1)))  # zero pad if needed

            windowed = x1 * win

            # Check if the windowed frame length is odd and pad with zero if necessary
            if len(windowed) % 2 != 0:
                windowed = np.append(windowed, 0.0) # Pad with a single zero

            spectrum = es.Spectrum(size=fft_size)
            spec = spectrum(windowed)

            mag = np.abs(spec)
            mag_db = 20 * np.log10(mag + 1e-10)
            peak_detect = es.PeakDetection(threshold=t)
            peaks_bin_raw, _ = peak_detect(mag_db)

            # Convert the raw output of peaks_bin to a numpy array of integers
            # to ensure it's a valid index for slicing.
            peaks_bin = np.array(peaks_bin_raw, dtype=int)

            # Proceed only if peaks were detected
            if len(peaks_bin) > 0:
                freqs = np.array(peaks_bin) * fs / fft_size
                mags = mag[peaks_bin]

                valid_idx = np.where((freqs >= band[0]) & (freqs < band[1]))[0]
                frame_peaks_freqs.extend(freqs[valid_idx])
                frame_peaks_mags.extend(mags[valid_idx])

        if frame_peaks_freqs:
            sort_idx = np.argsort(frame_peaks_freqs)
            freqs_sorted = np.array(frame_peaks_freqs)[sort_idx]
            mags_sorted = np.array(frame_peaks_mags)[sort_idx]

            # Generate synthetic frame
            # The length of the output frame from SineModelSynth is H
            frame = synth(freqs_sorted, mags_sorted, np.zeros_like(mags_sorted))

            start = pin - H // 2
            end = start + H
            if start >= 0 and end <= len(y):
                y[start:end] += frame[:H]
            # Handle the case where the synthetic frame might be shorter than H at the end of the signal
            elif start >= 0 and start < len(y) and end > len(y):
                valid_length = len(y) - start
                y[start:] += frame[:valid_length]

        pin += H

    return np.real(y).astype(np.float32)

In [ ]:
from google.colab import files
uploaded = files.upload()

Saving piano_slow.wav to piano_slow.wav


In [ ]:
# base line sinusoidal analysis/synthesis
### set the parameters
input_file = 'piano_slow.wav' # Replace with your desired input file name
M = [4095, 2047, 1023] # Example window sizes
N = [4096, 2048, 1024] # Example FFT sizes, power of 2 >= M
t = -40 # Example peak detection threshold in dB
B = [[0, 1000], [1000, 5000], [5000, 22050]] # Example frequency bands in Hz
window_type = 'blackman' # Example window type

# Load the audio file and get sample rate
loader = es.EasyLoader(filename=input_file)
audio = loader()
# Access sample_rate from the loaded audio object
# The output of EasyLoader is a numpy array, which does not have a sample_rate attribute.
# We assume a standard sample rate of 44100 Hz.
fs = 44100
# Convert to mono by averaging channels if it's not mono
if len(audio.shape) > 1:
    x = np.mean(audio, axis=1)
else:
    x = audio


# Generate the three windows
w = [get_window(window_type, M[0]),
     get_window(window_type, M[1]),
     get_window(window_type, M[2])]


# This line is incorrect because 'window' and 'M' are not defined in this scope
# and 'w' is already defined as a list of windows.
# Also, sineModel expects a single window and N, not lists.
# y = SM.sineModel(x, fs, w, N, t)

# To run the base line sineModel, you need to choose one set of parameters
# For example, using the parameters for the longest window:
y = SM.sineModel(x, fs, w[0], N[0], t)

ipd.display(ipd.Audio(data=x, rate=fs))
ipd.display(ipd.Audio(data=y, rate=fs))

In [ ]:
from google.colab import files
uploaded = files.upload()

Saving bird.wav to bird.wav


In [ ]:
# multiresolution sinusoidal analysis/synthesis
### set the parameters
import essentia.standard as es
import numpy as np
import scipy.signal
import IPython.display as ipd
from scipy.signal.windows import get_window

# --- Parameters ---
input_file = 'bird.wav'  # path to your mono or stereo wav file
M = [4095, 2047, 1023]    # window sizes for different bands
N = [4096, 2048, 1024]    # FFT sizes (next power of two)
t = -40                   # dB threshold for peak detection
B = [(0, 1000), (1000, 5000), (5000, 22050)]  # frequency bands

# --- Load audio file ---
loader = es.EasyLoader(filename=input_file)
audio = loader()

# Convert to mono if stereo
if len(audio.shape) > 1:
    x = np.mean(audio, axis=1)
else:
    x = audio

fs = 44100  # Use standard sample rate
x = x.astype(np.float32)  # Ensure float32

# --- Create analysis windows ---
from scipy.signal import get_window
window_types = ['blackman', 'blackman', 'blackman']
w = [get_window(window_types[i], M[i], fftbins=True) for i in range(3)]
w = [np.asarray(win, dtype=np.float32) for win in w]  # Convert for Essentia

# --- Run multi-resolution sinusoidal analysis ---
y = sineModelMultiRes(x, fs, w, N, t, B)

# --- Normalize output (for consistent loudness) ---
y = y / (np.max(np.abs(y)) + 1e-10)

# --- Playback ---
import IPython.display as ipd
ipd.display(ipd.Audio(data=y, rate=fs))



## Your explanation

